Vague words

1. Load vague words set
> Based on the QUARS++ work https://github.com/ISTI-FMT/QUARS_plus_plus

In [1]:
import requests
vaguewords = requests.get('https://raw.githubusercontent.com/ISTI-FMT/QUARS_plus_plus/master/jape_rules/vagueness/vague.lst')
vagues = []

for vword in vaguewords.text.splitlines():
  vagues = vagues + [vword.lower()]

vagues.pop()
vagues = list(dict.fromkeys(vagues))
print (vagues)

['abundant', 'acceptable', 'accordant', 'accurate', 'accurately', 'actual', 'adaptable', 'adequate', 'adequately', 'adjacent', 'advantageous', 'affordable', 'agile', 'agreeable', 'ambitious', 'ambivalent', 'ample', 'and so on', 'annoying', 'apparent', 'apposite', 'appreciable', 'appropriate', 'appropriately', 'approximate', 'approximately', 'apropos', 'apt', 'arduous', 'abstruse', 'abstrusely', 'as required', 'bad', 'badly', 'baffled', 'beautiful', 'befitting', 'boring', 'bothersome', 'brief', 'briefly', 'broad', 'broadly', 'businesslike', 'capable', 'capacious', 'careful', 'catchy', 'certain', 'challenging', 'cheap', 'clean', 'clear', 'clearly', 'closely', 'coarse-grained', 'coarse grained', 'coherent', 'colossal', 'comfortable', 'comfy', 'competent', 'complex', 'complicated', 'concise', 'concisely', 'concordant', 'confident', 'conformable', 'confused', 'congenial', 'congruent', 'congruous', 'considerable', 'consonant', 'conspicuous', 'cost-effective', 'cost effective', 'cost-efficien

2. Load user stories
> With another dataset: 
 * Load different Excel file
 * Consider whether there is a language column

In [2]:
import pandas as pd

res = pd.read_excel("tournify-stories.xlsx", sheet_name="tournify-stories")
res.head()

english = res[res['Language']=='en']
dutch = res[res['Language']=='nl']

3. Translate Dutch to English - run once, then save to file

In [ ]:
!pip install googletrans==4.0.0-rc1
from googletrans import Translator
translator = Translator()
 
english2 = []
for us in dutch['User story'].values.tolist():
  translated = translator.translate(us, dest = 'en').text
  english2.append(translated)

print (english2)

dict = {'dutch': dutch['User story'].values.tolist(), 'english': english2}  
       
df2 = pd.DataFrame(dict) 
    
# saving the dataframe 
df2.to_csv('translation.csv', index=False) 

In [4]:
col_list = ["english"]
df2 = pd.read_csv('translation.csv', usecols=col_list)


english2 = []
for index, stmt in df2.iterrows():
    english2.append(stmt["english"])




4. Find vague words
> Saves them to vague_hits.csv

In [5]:
import re

def string_found(string1, string2):
   if re.search(r"\b" + re.escape(string1) + r"\b", string2):
      return True
   return False


vague_hits = []

n = 1
for us in [*english['User story'].values.tolist(), *english2]:
  identified = False
  for word in vagues:
    if string_found(word, us.lower()):
      identified = True
      print (str(n) + " - " + word + " --- " + us)
      vague_hits.append([word, us])
  if (identified):
    n = n + 1

import csv
  
fields = ['Vague Word', 'Req'] 
    
with open('vague_hits.csv', 'w') as f:
      
    write = csv.writer(f)
    write.writerow(fields)
    write.writerows(vague_hits)

1 - fair --- As an organizer I want to the ranking take in consideration the points that I added for fair play. For example, in my ranking I now have 12 PTS for team A and 7 PTS in fair play for team A. I would like an option that allows me to take the 19 PTS (7+12) in consideration for the ranking instead of taking only the total of PTS (12 pts), so that I don't have to export and make another raking taking that in consideration and after import that file on the main page of the event. Doing that I won't have to change teams for the Bracket sections since all the points that I want will be taken into consideration
2 - valuable --- As an organizer I want to show the video replays of matches that have happened next to the results with a little icon. I want to also show the LIVE button for games currently in progress, so that I can get more people to watch the game and make the games valuable
3 - properly --- As an organizer I want to input scores of multiple sets of a tennis match, so t

5. Readability metrics

In [6]:
!pip install pip install textstat
import textstat
flesch = []
ari = []
combined = [*english['User story'].values.tolist(), *english2]
for us in combined:
  flesch.append(textstat.flesch_reading_ease(us))
  ari.append(textstat.automated_readability_index(us))

dict = {'us' : [*english['User story'].values.tolist(), *english2], 'flesch': flesch, 'ari': ari}  
       
df3 = pd.DataFrame(dict) 
df3.head()
df3.to_csv('readability.csv', index=False) 

     |████████████████████████████████| 101 kB 3.7 MB/s 
     |████████████████████████████████| 2.0 MB 34.5 MB/s 
